In [ ]:
import random

def generate_maze_matrix(N, M):
    matrix = [[0 for j in range(M)] for i in range(N)]
    for i in range(N):
        for j in range(M):
            # Randomly assign blocks
            matrix[i][j] = random.choice([0, 1])
    # Set start and goal states
    #matrix[0][0] = "s"
    #matrix[N-1][M-1] = "g"
    return matrix


In [ ]:
def print_maze(maze):
    for row in maze:
        for cell in row:
            if cell == 1:
                print("1", end=" ")
            else:
                print(cell, end=" ")
        print()
maze_matrix = generate_maze_matrix(10, 10)
print_maze(maze_matrix)

0 0 1 0 1 1 1 1 0 0 
0 1 0 1 1 0 1 1 0 0 
0 0 0 1 0 0 1 0 1 0 
0 0 0 0 0 1 0 1 0 1 
1 0 1 1 0 1 0 1 1 0 
1 1 1 1 0 1 0 1 0 0 
0 0 1 1 1 1 0 0 0 0 
1 0 1 1 1 1 0 1 1 1 
1 0 0 1 0 1 0 1 0 0 
0 0 0 0 0 1 1 1 0 0 


In [ ]:
import numpy as np
import random
from keras.models import Sequential
from keras.layers import Dense
from keras.optimizers import Adam

class DQNAgent:
    def __init__(self, state_size, action_size):
        self.state_size = state_size
        self.action_size = action_size
        self.memory = []
        self.gamma = 0.95
        self.epsilon = 1.0
        self.epsilon_decay = 0.995
        self.epsilon_min = 0.01
        self.learning_rate = 0.001
        self.model = self._build_model()

    def _build_model(self):
        model = Sequential()
        model.add(Dense(32, input_dim=self.state_size, activation='relu'))
        model.add(Dense(32, activation='relu'))
        model.add(Dense(self.action_size, activation='linear'))
        model.compile(loss='mse', optimizer=Adam(lr=self.learning_rate))
        return model

    def remember(self, state, action, reward, next_state, done):
        self.memory.append((state, action, reward, next_state, done))

    def act(self, state):
        if np.random.rand() <= self.epsilon:
            return random.randrange(self.action_size)
        act_values = self.model.predict(state)
        return np.argmax(act_values[0])

    def replay(self, batch_size):
        minibatch = random.sample(self.memory, batch_size)
        for state, action, reward, next_state, done in minibatch:
            target = reward
            if not np.any(done):
                target = (reward + self.gamma * np.amax(self.model.predict(next_state)[0]))
            target_f = self.model.predict(state)
            target_f[0][action] = target
            self.model.fit(state, target_f, epochs=1, verbose=0)
        if self.epsilon > self.epsilon_min:
            self.epsilon *= self.epsilon_decay

def get_possible_actions(state, maze):
    actions = []
    n, m = maze.shape
    x, y = state
    if y > 0 and maze[x][y-1] == 1:
        actions.append(0) # Move left
    if y < m-1 and maze[x][y+1] == 1:
        actions.append(1) # Move right
    if x > 0 and maze[x-1][y] == 1:
        actions.append(2) # Move up
    if x < n-1 and maze[x+1][y] == 1:
        actions.append(3) # Move down
    return actions

def get_reward(state, maze, goal_state):
    if np.all(state == goal_state):
        return 100
    if state[0] < 0 or state[0] >= maze.shape[0] or state[1] < 0 or state[1] >= maze.shape[1] or maze[state[0], state[1]] == 0:
        return -100
    return -1

def get_initial_state(maze):
    for i in range(maze.shape[0]):
        for j in range(maze.shape[1]):
            if maze[i][j] == 1:
                return (i, j)

def find_path_dqn(maze):
    start_state = get_initial_state(maze)
    goal_state = (maze.shape[0]-1, maze.shape[1]-1)
    state_size = 2
    action_size = 4
    agent = DQNAgent(state_size, action_size)
    batch_size = 32
    episodes = 1000
    for e in range(episodes):
        state = start_state
        state = np.reshape(state, [1, state_size])
        for time in range(100):
            action = agent.act(state)
            next_state = state.copy()
            if action == 0: # Move left
                next_state[0][1] -= 1
            elif action == 1: # Move right
                next_state[0][1] += 1
            elif action == 2: # Move up
                next_state[0][0] -= 1
            elif action == 3: # Move down
                next_state[0][0] += 1
            reward = get_reward(next_state[0], maze, goal_state)
            done = (next_state[0] == goal_state)
            next_state = np.reshape(next_state, [1, state_size])
            agent.remember(state, action, reward, next_state, done)
            state = next_state
            if np.any(done):
                break
    if len(agent.memory) > batch_size:
        agent.replay(batch_size)
    state = start_state
    state = np.reshape(state, [1, state_size])
    path = []
    while True:
        action = agent.act(state)
        next_state = state.copy()
        if action == 0: # Move left
            next_state[0][1] -= 1
        elif action == 1: # Move right
            next_state[0][1] += 1
        elif action == 2: # Move up
            next_state[0][0] -= 1
        elif action == 3: # Move down
            next_state[0][0] += 1
        path.append(tuple(next_state[0]))
        state = np.reshape(next_state, [1, state_size])
        if state[0][0] == goal_state[0] and state[0][1] == goal_state[1]:
            break
    return path

In [ ]:
maze = np.array([[1, 1, 1, 0, 1],
[1, 0, 1, 1, 1],
[1, 0, 0, 1, 1],
[1, 1, 1, 1, 1],
[0, 0, 1, 0, 1]])
path = find_path_dqn(maze)
print(path)

1/1 [==============================] - 0s 2ms/step


1/1 [==============================] - 0s 12ms/step


1/1 [==============================] - 0s 14ms/step


1/1 [==============================] - 0s 9ms/step


1/1 [==============================] - 0s 5ms/step


...

1/1 [==============================] - 0s 22ms/step


1/1 [==============================] - 0s 19ms/step


1/1 [==============================] - 0s 16ms/step


1/1 [==============================] - 0s 24ms/step


1/1 [==============================] - 0s 5ms/step
